<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#HyperSpy-Fitting-tutorial" data-toc-modified-id="HyperSpy-Fitting-tutorial-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>HyperSpy Fitting tutorial</a></span><ul class="toc-item"><li><span><a href="#Author:" data-toc-modified-id="Author:-1.1"><span class="toc-item-num">1.1&nbsp;&nbsp;</span>Author:</a></span><ul class="toc-item"><li><span><a href="#Terminology-and-relationships" data-toc-modified-id="Terminology-and-relationships-1.1.1"><span class="toc-item-num">1.1.1&nbsp;&nbsp;</span>Terminology and relationships</a></span></li></ul></li></ul></li><li><span><a href="#Generating-synthetic-data" data-toc-modified-id="Generating-synthetic-data-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Generating synthetic data</a></span><ul class="toc-item"><li><span><a href="#Two-peaks" data-toc-modified-id="Two-peaks-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Two peaks</a></span></li><li><span><a href="#Wobbly-peak" data-toc-modified-id="Wobbly-peak-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Wobbly peak</a></span><ul class="toc-item"><li><span><a href="#Importing" data-toc-modified-id="Importing-2.2.1"><span class="toc-item-num">2.2.1&nbsp;&nbsp;</span>Importing</a></span></li><li><span><a href="#How-do-I-....-again?" data-toc-modified-id="How-do-I-....-again?-2.2.2"><span class="toc-item-num">2.2.2&nbsp;&nbsp;</span>How do I .... again?</a></span></li><li><span><a href="#Fitting-in-HyperSpy-(detailed)" data-toc-modified-id="Fitting-in-HyperSpy-(detailed)-2.2.3"><span class="toc-item-num">2.2.3&nbsp;&nbsp;</span>Fitting in HyperSpy (detailed)</a></span></li></ul></li><li><span><a href="#Fitting-multi-dimensional-signals" data-toc-modified-id="Fitting-multi-dimensional-signals-2.3"><span class="toc-item-num">2.3&nbsp;&nbsp;</span>Fitting multi-dimensional signals</a></span></li><li><span><a href="#Goodness-of-fit" data-toc-modified-id="Goodness-of-fit-2.4"><span class="toc-item-num">2.4&nbsp;&nbsp;</span>Goodness of fit</a></span></li><li><span><a href="#Defining-your-own-components" data-toc-modified-id="Defining-your-own-components-2.5"><span class="toc-item-num">2.5&nbsp;&nbsp;</span>Defining your own components</a></span></li></ul></li></ul></div>

# HyperSpy Fitting tutorial

This tutorial shows the basics of model (currently only 1D) fitting in HyperSpy from the grounds up. All data is artificial and can be generated by running the code <a href='#two_peaks'>at the end</a> of the notebook.

__Required version:__

    HyperSpy 1.3

## Author:

* 25/04/2017 Francisco de la Peña - Updated it for Diamond Light Source workshop
  * Fix TOC and internal links
  * Redifine the ``sin`` component to facilite setting the initial parameters
* 13/04/2015 Tomas Ostasevicius - Developed for HyperSpy workshop at University of Cambridge
* 01/06/2016 Tomas Ostasevicius - updated and expanded for HyperSpy workshop at Scandem conference 2016
* 22/07/2016 Tomas Ostasevicius - updated for HyperSpy version 1.0

<a id='terms'></a>
### Terminology and relationships
[Go to TOC](#Table-of-Contents)

In order to use fitting in HyperSpy more effectively, it is useful to understand our structure for curve fitting.

There are three main things, related to fitting:

__1. Model__
can be thought of as a simple box (cooking pot), where we have to put our ingredients. Without anything inside, it is not of much use in this case. Once we add some things to it and mix it a bit (do the actual fitting), however, we have our complete dish!

__2. Component__ is the main building block (ingredient) of our model. Here we mix and match what components we need (or want) for the particular case of signal. 

Examples: 
- Lorentzian (Cauchy)
- Gaussian
- Voigt (a combination of Lorentzian and Gaussian)
- Offset (i.e. constant background)
- Exponential function
- ...
- [create your own or use the very specialised ones!]

Each of the components is ultimately just a function that has variables that change the (shape of the) output. Such a variable in HyperSpy is called a __parameter__


__3. Parameter__ is the knob that the fitting routine adjusts for a good fit. Each component must include at least one parameter in order to be able to change when fitting. A parameter is also the object that we may limit or have to adjust when the result of the fit is not satisfactory. 

Ultimately, a parameter is the only important thing, as far as the fitting is concerned - components are just smart and convenient boxes to combine parameters into functions, and a model is just a box for a collection of components.

For now, let's just keep the rough structure in our heads and look at other things!



# Generating synthetic data

<a id='two_peaks'></a>
## Two peaks


[[Go to TOC]](#Table-of-Contents)


In [ ]:
from scipy.ndimage import gaussian_filter
import numpy as np
import hyperspy.api as hs
# set the parameters:
blurs = [0., 1.]
radius = 3  #radius of a different region
domain = 10 #size of the square domain
small_centres = (500, 900)
small_amplitudes = (8000,  5000)

# work:
total = None
cent = (domain//2, domain//2)
y,x = np.ogrid[-cent[0]:domain-cent[0], -cent[1]:domain-cent[1]]
mask = x*x + y*y <= radius*radius
for blur in blurs:

    s = hs.signals.Signal1D(np.ones((domain,domain, 1024)))
    cent = tuple([int(0.5*i) for i in s.data.shape[:-1]])
    m0 = s.create_model()
    gs01 = hs.model.components1D.Gaussian()
    m0.append(gs01)
    gs01.sigma.value = 300
    gs01.centre.map['values'][:] = (np.random.random((domain,domain)) - 0.5)*50 + small_centres[0]
    gs01.centre.map['is_set'][:] = True
    gs01.A.map['values'][:] = 1000 * np.random.random((domain,domain)) + 300000
    gs01.A.map['is_set'][:] = True

    gs02 = hs.model.components1D.Gaussian()
    m0.append(gs02)
    gs02.sigma.value = 30
    gs02.centre.map['values'][:] = (np.random.random((domain,domain)) - 0.5)*50 +  small_centres[1]

    gs02.centre.map['values'][mask] = (np.random.random(gs02.centre.map['values'][mask].shape) - 0.5)*50 + 700
    #gs02.centre.map['values'][10:20,10:20] = (np.random.random((10,10)) - 0.5)*100 + 200

    gs02.centre.map['values'] = gaussian_filter(gs02.centre.map['values'], blur)
    gs02.centre.map['is_set'][:] = True
    gs02.A.map['values'][:] = small_amplitudes[0]
    gs02.A.map['values'][mask] = small_amplitudes[1]
    gs02.A.map['values'] = gaussian_filter(gs02.A.map['values'], blur)
    gs02.A.map['is_set'][:] = True
    s11 = m0.as_signal()
    if total is None:
        total = s11.data.copy()
    else:
        total = np.concatenate((total, s11.data), axis=1)
        
s = hs.signals.Signal1D(total)
s.metadata.General.author = 'Tomas Ostasevicius'
s.metadata.General.title = 'Two gaussians'

s.add_poissonian_noise()
s.estimate_poissonian_noise_variance()
s.axes_manager[0].name = "x"
s.axes_manager[0].units = "nm"
s.axes_manager[1].name = "y"
s.axes_manager[1].units = "nm"

s.axes_manager[2].name = "Energy"
s.axes_manager[2].name = "eV"
s.axes_manager[2].scale = 0.1

s.inav[5,5].save("two_peaks", overwrite=True)
s.inav[10:20,:].save("smoothly_moving_peaks", overwrite=True)

<a id='wobbly_peak'></a>
## Wobbly peak

[[Go to TOC]](#Table-of-Contents)


In [ ]:
import numpy as np
import hyperspy.api as hs

k = 1
alpha = 15
amp = 3

gaus_position = 15
gaus_width = 5
gaus_A = 300

gradient = 0.6
offset= 3

sin_component = hs.model.components1D.Expression('A * sin(k*x + alpha)', name='sin', k=k,
                                               alpha=alpha, A=amp)
gaus = hs.model.components1D.Gaussian(A=gaus_A, sigma=gaus_width, centre=gaus_position)

poly = hs.model.components1D.Polynomial(1)

poly.coefficients.value = (gradient, offset)

axis = np.linspace(0, 30, 3000, dtype='double')

result = sin_component.function(axis)+ gaus.function(axis) + poly.function(axis)
s = hs.signals.Signal1D(result)
s.axes_manager[0].name = 'x'
s.axes_manager[0].scale = 0.1
s.axes_manager[0].offset = 0

s.metadata.General.author = 'Tomas Ostasevicius'
s.metadata.General.title = 'Sin + poly(2) + Gaussian'
s.save('wobbly_peak', overwrite=True)